In [28]:
#%pylab notebook
%config InlineBackend.figure_format = 'retina'

#Pandas, numpy & Dates
import pandas as pd
import numpy as np
from datetime import datetime, date, timedelta
from numpy import arange

#Working directory tools
import os
from os import listdir
cwd = os.path.abspath('../..')

#Max display (monitor)
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:80% !important; }</style>")) #70%

#Load custom functions
exec(open(cwd + "\\Scripts\\Functions.py").read())

#Stats (skewness and kurtosis)
import scipy
from scipy.stats import skew
from scipy.stats import kurtosis

from scipy import stats
from scipy import integrate

#Widgets & plots (as widgets)
import ipywidgets as widgets
from ipywidgets import ToggleButtons, VBox, HBox, HTML

from bqplot.interacts import (FastIntervalSelector, 
                              IndexSelector, BrushIntervalSelector,
                              BrushSelector, MultiSelector, 
                              LassoSelector, PanZoom, HandDraw)

#interaction
from traitlets import link
from IPython.display import HTML, display, clear_output

#File exploring window
from tkinter import Tk, filedialog 
from tkinter import *

from bqplot import *

from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator

In [29]:
#Get all csv files to load the data
CsvFilesList = os.listdir(cwd + "\\Csv Files")

#Raw to Clean data
FFsDataList = Raw2CleaFFsDat(CsvFilesList, cwd)

#Dropdown and scrollable menus tickers lists
TickerSets, TickerSets_2, TickersDict, TickersDict_2, FactorList = MenuTickerList(FFsDataList)

#FedSpeak database
FedSpeakBBDD = pd.read_csv(cwd + "\\Studies\\Dossier\\FedSpeak.csv", sep = ';', 
                           index_col = 0, encoding = 'ISO-8859-1')

#Border widget
BorderHtmlW = widgets.HTML(('<hr style="border: 0 none;background-color:' + 
                            '#0070C0;height: 4px;opacity: 1;margin-top: 0px;margin-bottom:0px;"/>'))

BorderHtmlW = widgets.HTML(('<hr style="border: 0 none;background-color:' + 
                            '#0070C0;height: 4px;opacity: 0.7;margin-top: 0px;margin-bottom:0px;"/>'))

#<hr style="border: 0 none;background-color: #0070C0;height: 5px;opacity: 0.8;"/>

In [30]:
HTML(
'''<script>
  function code_toggle() {
    if (code_shown){
      $('div.input').hide('500');
      $('#toggleButton').val('Show Code')
    } else {
      $('div.input').show('500');
      $('#toggleButton').val('Hide Code')
    }
    code_shown = !code_shown
  }

  $( document ).ready(function(){
    code_shown=false;
    $('div.input').hide()
  });
</script>
<form action="javascript:code_toggle()"><input type="submit" id="toggleButton" value="Show Code"></form>''')

In [31]:
#Plot data
############################################################ 
Date_1 = '2018-1-1'
Date_2 = '2018-10-3'

Summary = FFsDataList['Hikes_Generic_Data'][Date_1:Date_2].describe() 

#Average curve +- 1 std
AverageCurve = np.array(Summary.loc['mean'])  
Minus1Std = np.array(Summary.loc['mean'] - Summary.loc['std']) 
Plus1Std = np.array(Summary.loc['mean'] + Summary.loc['std']) 

#Tickers
Scatt_x_data = ['H' + str(i) for i in range(1, len(AverageCurve) + 1)]
Scatt_y_data = AverageCurve


Date_1_2 = '2018-11-28'
Date_2_2 = '2019-9-6'

Summary_2 = FFsDataList['Hikes_Generic_Data'][Date_1_2:Date_2_2].describe() 

#Average curve +- 1 std
AverageCurve_2 = np.array(Summary_2.loc['mean'])  
Minus1Std_2 = np.array(Summary_2.loc['mean'] - Summary_2.loc['std']) 
Plus1Std_2 = np.array(Summary_2.loc['mean'] + Summary_2.loc['std']) 

#Tickers
Scatt_x_data_2 = ['H' + str(i) for i in range(1, len(AverageCurve_2) + 1)]
Scatt_y_data_2 = AverageCurve_2
############################################################ 

#Step 1: Scales & Axes
############################################################ 
#Scales 
Scatt_x = OrdinalScale()
Scatt_y = LinearScale()

#X-Axis
ax_x = Axis(scale = Scatt_x, 
            tick_format = '', 
            label_location = 'end', 
            label = 'Hike',
            num_ticks = 14,
            tick_style = {'font-size': '12px'}, 
            label_offset = '40px')

#Y-Axis
ax_y = Axis(scale = Scatt_y, 
            orientation = 'vertical', 
            tick_format = '.1f', 
            label_location = 'end',
            label = 'bps', 
            grid_color = '#EDEDED',
            tick_style = {'font-size': '12px'}, 
            label_offset = '40px')
############################################################

#Step 2: Marks (plots)
############################################################     
#Marks, scatter plot (legs)
Scatt = Scatter(x = Scatt_x_data, 
                y = Scatt_y_data,               
                scales = {'x': Scatt_x, 
                          'y': Scatt_y},
                colors = ['#01B0F0'],
                default_size = 80,
                default_opacities = [0.7], 
                stroke='black', 
                unhovered_style={'opacity': 0.2})

#Curve interpolation (mean curve)
lin = Lines(x = Scatt.x, y = Scatt.y, 
            scales = {'x': Scatt_x, 'y' : Scatt_y},
            colors = ['#01B0F0'], 
            stroke_width = 2, interpolation = 'cardinal')

#Curve interpolation (+- 1 std)
lin2 = Lines(x = Scatt.x, y = [Minus1Std, Plus1Std], 
            scales = {'x': Scatt_x, 'y' : Scatt_y}, 
            colors = ['#DE2369'], 
            stroke_width = 0, 
            interpolation = 'cardinal', 
            fill = 'between', 
            fill_colors = ['#0070C0'], 
            fill_opacities = ['0.1'])



#Marks, scatter plot (legs)
Scatt_2 = Scatter(x = Scatt_x_data_2, 
                y = Scatt_y_data_2,               
                scales = {'x': Scatt_x, 
                          'y': Scatt_y},
                colors = ['#01B0F0'],
                default_size = 80,
                default_opacities = [0.7], 
                stroke='black', 
                unhovered_style={'opacity': 0.2})

#Curve interpolation (mean curve)
lin_2 = Lines(x = Scatt_2.x, y = Scatt_2.y, 
            scales = {'x': Scatt_x, 'y' : Scatt_y},
            colors = ['#01B0F0'], 
            stroke_width = 2, interpolation = 'cardinal')

#Curve interpolation (+- 1 std)
lin2_2 = Lines(x = Scatt_2.x, y = [Minus1Std_2, Plus1Std_2], 
            scales = {'x': Scatt_x, 'y' : Scatt_y}, 
            colors = ['#DE2369'], 
            stroke_width = 0, 
            interpolation = 'cardinal', 
            fill = 'between', 
            fill_colors = ['#DE2369'], 
            fill_opacities = ['0.1'])
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['', '.2f'], 
                 labels = ['Hike', 'Price'])

#Set the tooltip interaction(s)
Scatt.tooltip = def_tt
Scatt.interactions = {'hover': 'tooltip'}

#Set the tooltip interaction(s)
Scatt_2.tooltip = def_tt
Scatt_2.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################
#initial Figure
figure1 = Figure(marks = [lin, lin2, Scatt, lin_2, lin2_2, Scatt_2], 
                 axes = [ax_x, ax_y])

#Figure Title
figure1.title =  'Figure 1: ' + 'Average Hikes Curve: Before and After'

#Figure layout (except size attributes, defined on section 4) 
figure1.title_style = {'font-size': '13px'}
figure1.background_style = {'fill': 'white'} 

figure1.fig_margin = {'top':40, 'bottom':50, 'left':50, 'right':10}
figure1.layout.width = '60%'
figure1.layout.height = '760px'
figure1.legend_location = 'top-left'
figure1.layout.left = '120px'

############################################################
############################################################
############################################################
############################################################

DesriptionBox_1 = widgets.HTML('<p> <li> <b> Rate Hikes Regime (blue): </b>  <br>' + 
                               'From January 2018 through September, up until the famous "Long way from Neutral"' +
                               ' phrase was pushed by Fed Chair Powell on a PBS News Hour Q&A session, on the 3rd of October, 2018. </li>' + 
                               '<br>' +
                                   '<ul style = "color: #125CB2; font-size: 16px; font-weight: bold;">' + 
                                       '<li> Clear Pc bias  </li>' +
                                       '<li> Vol across the curve </li>' + 
                                       '<li> Strong rollup </li>' +
                                   '</ul>' + 
                               '<br>' '</p>' + 
                               '<p> <li> <b> Rate Cuts Regime (red): </b>  <br>' + 
                               'Beginning on the 28th of November, when Fed Chair Powell confirmed the dovish shift ' + 
                               'Fed officials had been showcasing throughout November 2018, and the first cuts ' + 
                               'began to appear on the Hikes curve. </li>' + 
                               '<br>' +
                                   '<ul style = "color: #125CB2; font-size: 16px; font-weight: bold;">' + 
                                       '<li> First cuts get priced </li>' +
                                       '<li> No clear PcBias </li>' + 
                                       '<li> Lack of Vol on the back </li>' + 
                                       '<li> Very strong rolldown </li>' + 
                                   '</ul>' + 
                               '</p>')

DesriptionBox_1.layout.width = '20%'
DesriptionBox_1.layout.height = '500px'
DesriptionBox_1.layout.left = '180px'
DesriptionBox_1.layout.top = '40px'

In [32]:
VBox([widgets.HTML('<a id="Figure_1"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> Two Monetary Policy Regimes: </b>' + 
                   'Average expected hikes curve +/- one standard deviation. </p>'),
      BorderHtmlW, HBox([figure1, DesriptionBox_1]), BorderHtmlW])

In [33]:
#Plot data
############################################################  
Date_1 = '2018-11-28'
Date_2 = '2019-1-3'

Summary = FFsDataList['Hikes_Generic_Data'][Date_1:Date_2].describe() 

#Average curve +- 1 std
AverageCurve = np.array(Summary.loc['mean'])  
Minus1Std = np.array(Summary.loc['mean'] - Summary.loc['std']) 
Plus1Std = np.array(Summary.loc['mean'] + Summary.loc['std']) 

#Tickers
Scatt_x_data = ['H' + str(i) for i in range(1, len(AverageCurve) + 1)]
Scatt_y_data = AverageCurve
############################################################ 

#Step 1: Scales & Axes
############################################################ 
#Scales 
Scatt_x = OrdinalScale()
Scatt_y = LinearScale()

#X-Axis
ax_x = Axis(scale = Scatt_x, 
            tick_format = '', 
            label_location = 'end', 
            label = 'Hike',
            num_ticks = 8,
            tick_style = {'font-size': '11px'}, 
            label_offset = '40px')

#Y-Axis
ax_y = Axis(scale = Scatt_y, 
            orientation = 'vertical', 
            tick_format = '.1f', 
            label_location = 'end',
            label = 'bps', 
            grid_color = '#EDEDED',
            tick_style = {'font-size': '12px'}, 
            label_offset = '40px')
############################################################

#Step 2: Marks (plots)
############################################################     
#Marks, scatter plot (legs)
Scatt = Scatter(x = Scatt_x_data, 
                y = Scatt_y_data,               
                scales = {'x': Scatt_x, 
                          'y': Scatt_y},
                colors = ['#01B0F0'],
                default_size = 80,
                default_opacities = [0.7], 
                stroke='black', 
                unhovered_style={'opacity': 0.2})

#Curve interpolation (mean curve)
lin = Lines(x = Scatt.x, y = Scatt.y, 
            scales = {'x': Scatt_x, 'y' : Scatt_y},
            colors = ['#01B0F0'], 
            stroke_width = 2, interpolation = 'cardinal')

#Curve interpolation (+- 1 std)
lin2 = Lines(x = Scatt.x, y = [Minus1Std, Plus1Std], 
            scales = {'x': Scatt_x, 'y' : Scatt_y}, 
            colors = ['#DE2369'], 
            stroke_width = 2.5, 
            interpolation = 'cardinal', 
            fill = 'between', 
            fill_colors = ['#0070C0'], 
            fill_opacities = ['0.1'])
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['', '.2f'], 
                 labels = ['Hike', 'Price'])

#Set the tooltip interaction(s)
Scatt.tooltip = def_tt
Scatt.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################
#initial Figure
figure2 = Figure(marks = [lin, lin2, Scatt], 
                 axes = [ax_x, ax_y])

#Figure Title
figure2.title =  'Figure 2: ' + Date_1 + ' to ' + Date_2

#Figure layout (except size attributes, defined on section 4) 
figure2.title_style = {'font-size': '13px'}
figure2.background_style = {'fill': 'white'} 

figure2.fig_margin = {'top':40, 'bottom':50, 'left':50, 'right':10}
figure2.layout.width = '45%'
figure2.layout.height = '380px'
figure2.legend_location = 'top-left'
figure2.layout.left = '30px'


############################################################
############################################################
############################################################

#Plot data
############################################################  
Date_1_2 = '2018-11-28'
Date_2_2 = '2019-3-27'

Summary_2 = FFsDataList['Hikes_Generic_Data'][Date_1_2:Date_2_2].describe() 

#Average curve +- 1 std
AverageCurve = np.array(Summary_2.loc['mean'])  
Minus1Std = np.array(Summary_2.loc['mean'] - Summary_2.loc['std']) 
Plus1Std = np.array(Summary_2.loc['mean'] + Summary_2.loc['std']) 

#Tickers
Scatt_x_data = ['H' + str(i) for i in range(1, len(AverageCurve) + 1)]
Scatt_y_data = AverageCurve
############################################################ 

#Step 1: Scales & Axes
############################################################ 
#Scales 
Scatt_x = OrdinalScale()
Scatt_y = LinearScale()

#X-Axis
ax_x = Axis(scale = Scatt_x, 
            tick_format = '', 
            label_location = 'end', 
            label = 'Hike',
            num_ticks = 8,
            tick_style = {'font-size': '11px'}, 
            label_offset = '40px')

#Y-Axis
ax_y = Axis(scale = Scatt_y, 
            orientation = 'vertical', 
            tick_format = '.1f', 
            label_location = 'end',
            label = 'bps', 
            grid_color = '#EDEDED',
            tick_style = {'font-size': '12px'}, 
            label_offset = '40px')
############################################################

#Step 2: Marks (plots)
############################################################     
#Marks, scatter plot (legs)
Scatt = Scatter(x = Scatt_x_data, 
                y = Scatt_y_data,               
                scales = {'x': Scatt_x, 
                          'y': Scatt_y},
                colors = ['#01B0F0'],
                default_size = 80,
                default_opacities = [0.7], 
                stroke='black', 
                unhovered_style={'opacity': 0.2})

#Curve interpolation (mean curve)
lin = Lines(x = Scatt.x, y = Scatt.y, 
            scales = {'x': Scatt_x, 'y' : Scatt_y},
            colors = ['#01B0F0'], 
            stroke_width = 2, interpolation = 'cardinal')

#Curve interpolation (+- 1 std)
lin2 = Lines(x = Scatt.x, y = [Minus1Std, Plus1Std], 
            scales = {'x': Scatt_x, 'y' : Scatt_y}, 
            colors = ['#DE2369'], 
            stroke_width = 2.5, 
            interpolation = 'cardinal', 
            fill = 'between', 
            fill_colors = ['#0070C0'], 
            fill_opacities = ['0.1'])
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['', '.2f'], 
                 labels = ['Hike', 'Price'])

#Set the tooltip interaction(s)
Scatt.tooltip = def_tt
Scatt.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################
#initial Figure
figure3 = Figure(marks = [lin, lin2, Scatt], 
                 axes = [ax_x, ax_y])

#Figure Title
figure3.title = 'Figure 3: ' + Date_1_2 + ' to ' + Date_2_2

#Figure layout (except size attributes, defined on section 4) 
figure3.title_style = {'font-size': '13px'}
figure3.background_style = {'fill': 'white'} 

figure3.fig_margin = {'top':40, 'bottom':50, 'left':50, 'right':10}
figure3.layout.width = '45%'
figure3.layout.height = '380px'
figure3.legend_location = 'top-left'
figure3.layout.left = '60px'


############################################################  
############################################################  
############################################################  


#Plot data
############################################################   
Date_1_3 = '2018-11-28'
Date_2_3 = '2019-6-3'

Summary_3 = FFsDataList['Hikes_Generic_Data'][Date_1_3:Date_2_3].describe() 

#Average curve +- 1 std
AverageCurve = np.array(Summary_3.loc['mean'])  
Minus1Std = np.array(Summary_3.loc['mean'] - Summary_3.loc['std']) 
Plus1Std = np.array(Summary_3.loc['mean'] + Summary_3.loc['std']) 

#Tickers
Scatt_x_data = ['H' + str(i) for i in range(1, len(AverageCurve) + 1)]
Scatt_y_data = AverageCurve
############################################################ 

#Step 1: Scales & Axes
############################################################ 
#Scales 
Scatt_x = OrdinalScale()
Scatt_y = LinearScale()

#X-Axis
ax_x = Axis(scale = Scatt_x, 
            tick_format = '', 
            label_location = 'end', 
            label = 'Hike',
            num_ticks = 8,
            tick_style = {'font-size': '11px'}, 
            label_offset = '40px')

#Y-Axis
ax_y = Axis(scale = Scatt_y, 
            orientation = 'vertical', 
            tick_format = '.1f', 
            label_location = 'end',
            label = 'bps', 
            grid_color = '#EDEDED',
            tick_style = {'font-size': '12px'}, 
            label_offset = '40px')
############################################################

#Step 2: Marks (plots)
############################################################     
#Marks, scatter plot (legs)
Scatt = Scatter(x = Scatt_x_data, 
                y = Scatt_y_data,               
                scales = {'x': Scatt_x, 
                          'y': Scatt_y},
                colors = ['#01B0F0'],
                default_size = 80,
                default_opacities = [0.7], 
                stroke='black', 
                unhovered_style={'opacity': 0.2})

#Curve interpolation (mean curve)
lin = Lines(x = Scatt.x, y = Scatt.y, 
            scales = {'x': Scatt_x, 'y' : Scatt_y},
            colors = ['#01B0F0'], 
            stroke_width = 2, interpolation = 'cardinal')

#Curve interpolation (+- 1 std)
lin2 = Lines(x = Scatt.x, y = [Minus1Std, Plus1Std], 
            scales = {'x': Scatt_x, 'y' : Scatt_y}, 
            colors = ['#DE2369'], 
            stroke_width = 2.5, 
            interpolation = 'cardinal', 
            fill = 'between', 
            fill_colors = ['#0070C0'], 
            fill_opacities = ['0.1'])
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['', '.2f'], 
                 labels = ['Hike', 'Price'])

#Set the tooltip interaction(s)
Scatt.tooltip = def_tt
Scatt.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################
#initial Figure
figure4 = Figure(marks = [lin, lin2, Scatt], 
                 axes = [ax_x, ax_y])

#Figure Title
figure4.title = 'Figure 4: ' + Date_1_3 + ' to ' + Date_2_3

#Figure layout (except size attributes, defined on section 4) 
figure4.title_style = {'font-size': '13px'}
figure4.background_style = {'fill': 'white'} 

figure4.fig_margin = {'top':40, 'bottom':50, 'left':50, 'right':10}
figure4.layout.width = '45%'
figure4.layout.height = '380px'
figure4.legend_location = 'top-left'
figure4.layout.left = '30px'


############################################################  
############################################################  
############################################################  


#Plot data
############################################################   
Date_1_4 = '2018-11-28'
Date_2_4 = '2019-9-3'

Summary_4 = FFsDataList['Hikes_Generic_Data'][Date_1_4:Date_2_4].describe() 

#Average curve +- 1 std
AverageCurve = np.array(Summary_4.loc['mean'])  
Minus1Std = np.array(Summary_4.loc['mean'] - Summary_4.loc['std']) 
Plus1Std = np.array(Summary_4.loc['mean'] + Summary_4.loc['std']) 

#Tickers
Scatt_x_data = ['H' + str(i) for i in range(1, len(AverageCurve) + 1)]
Scatt_y_data = AverageCurve
############################################################ 

#Step 1: Scales & Axes
############################################################ 
#Scales 
Scatt_x = OrdinalScale()
Scatt_y = LinearScale()

#X-Axis
ax_x = Axis(scale = Scatt_x, 
            tick_format = '', 
            label_location = 'end', 
            label = 'Hike',
            num_ticks = 8,
            tick_style = {'font-size': '11px'}, 
            label_offset = '40px')

#Y-Axis
ax_y = Axis(scale = Scatt_y, 
            orientation = 'vertical', 
            tick_format = '.1f', 
            label_location = 'end',
            label = 'bps', 
            grid_color = '#EDEDED',
            tick_style = {'font-size': '12px'}, 
            label_offset = '40px')
############################################################

#Step 2: Marks (plots)
############################################################     
#Marks, scatter plot (legs)
Scatt = Scatter(x = Scatt_x_data, 
                y = Scatt_y_data,               
                scales = {'x': Scatt_x, 
                          'y': Scatt_y},
                colors = ['#01B0F0'],
                default_size = 80,
                default_opacities = [0.7], 
                stroke='black', 
                unhovered_style={'opacity': 0.2})

#Curve interpolation (mean curve)
lin = Lines(x = Scatt.x, y = Scatt.y, 
            scales = {'x': Scatt_x, 'y' : Scatt_y},
            colors = ['#01B0F0'], 
            stroke_width = 2, interpolation = 'cardinal')

#Curve interpolation (+- 1 std)
lin2 = Lines(x = Scatt.x, y = [Minus1Std, Plus1Std], 
            scales = {'x': Scatt_x, 'y' : Scatt_y}, 
            colors = ['#DE2369'], 
            stroke_width = 2.5, 
            interpolation = 'cardinal', 
            fill = 'between', 
            fill_colors = ['#0070C0'], 
            fill_opacities = ['0.1'])
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['', '.2f'], 
                 labels = ['Hike', 'Price'])

#Set the tooltip interaction(s)
Scatt.tooltip = def_tt
Scatt.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################
#initial Figure
figure5 = Figure(marks = [lin, lin2, Scatt], 
                 axes = [ax_x, ax_y])

#Figure Title
figure5.title = 'Figure 5: ' + Date_1_4 + ' to ' + Date_2_4

#Figure layout (except size attributes, defined on section 4) 
figure5.title_style = {'font-size': '13px'}
figure5.background_style = {'fill': 'white'} 

figure5.fig_margin = {'top':40, 'bottom':50, 'left':50, 'right':10}
figure5.layout.width = '45%'
figure5.layout.height = '380px'
figure5.legend_location = 'top-left'
figure5.layout.left = '60px'

In [34]:
DesriptionBox_2 = widgets.HTML('<p> <b> Rate Hikes Curve 2019 Progression: </b> <br>' + 
                               'Spanning from 28/11/2018 ("Just below Neutral"), through September 2019. Each plot includes data up to ' + 
                               'each market crash in 2019:' +
                               '<br>' +
                               '<br>' +
                                   '<ul style = "color: #125CB2; font-size: 16px; font-weight: bold;">' + 
                                       '<li> Figure 2: Christmas Rally  </li>' +
                                       '<li> Figure 3: Mar FOMC meeting </li>' + 
                                       '<li> Figure 4: May FOMC Minutes </li>' +
                                       '<li> Figure 5: Aug Trump Tweets </li>' +
                                   '</ul>' + 
                               '<br>' '</p>' + 
                               '<p>' + 
                               'Some takes on the curve progression: ' + 
                               '<br>' +
                               '<br>' +
                                   '<ul style = "color: #125CB2; font-size: 16px; font-weight: bold;">' + 
                                       '<li> Flattening after each crash </li>' +
                                       '<li> Higher front vol </li>' + 
                                       '<li> Smaller back end vol </li>' + 
                                       '<li> Erratic Pc Bias (tradeable) </li>' + 
                                       '<li> Clear rolldown </li>' + 
                                   '</ul>' + 
                               '</p>')

DesriptionBox_2.layout.width = '20%'
DesriptionBox_2.layout.height = '380px'
DesriptionBox_2.layout.left = '20px'
DesriptionBox_2.layout.top = '40px'
#DesriptionBox_2.layout.border = 'solid black'

In [35]:
VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> Expected Hikes Curve Progression after each crash: </b>' + 
                   'Average expected hikes curve +/- one standard deviation. </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure2, figure3], layout = {'width': '100%'}), 
                               HBox([figure4, figure5], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_2]), BorderHtmlW])

In [36]:
#2019 Hikes set
#FFsDataList['Hikes_Specific_Data'].iloc[:, -20:].head()
HikeSet = ['Z18', 'F19', 'H19', 'K19', 'M19', 'Q19', 'U19', 'V19', 'Z19']
Hikes2019 = FFsDataList['Hikes_Specific_Data'].loc[:, HikeSet]['2018':'2019']

#Start date
#StartD = '2018-10-3'
StartD = '2018-1-3'

#Data frames (one for each noPc meeting)
Df_1 = Hikes2019[StartD:GetSpreadDates('Z18', FFsDataList)[1][1]].loc[:, ('Z18', 'F19', 'H19')]
Df_2 = Hikes2019[StartD:GetSpreadDates('H19', FFsDataList)[1][1]].loc[:, ('H19', 'K19', 'M19')]
Df_3 = Hikes2019[StartD:GetSpreadDates('M19', FFsDataList)[1][1]].loc[:, ('M19', 'Q19', 'U19')]
Df_4 = Hikes2019[StartD:GetSpreadDates('U19', FFsDataList)[1][1]].loc[:, ('U19', 'V19', 'Z19')]

#Interpolations (one for each noPc meeting)
Interp_1 = Df_1.iloc[:, 0] + ((Df_1.iloc[:, 1] - Df_1.iloc[:, 0]) / 2)
Interp_2 = Df_2.iloc[:, 0] + ((Df_2.iloc[:, 1] - Df_2.iloc[:, 0]) / 2)
Interp_3 = Df_3.iloc[:, 0] + ((Df_3.iloc[:, 1] - Df_3.iloc[:, 0]) / 2)
Interp_4 = Df_4.iloc[:, 0] + ((Df_4.iloc[:, 1] - Df_4.iloc[:, 0]) / 2)

#Interpolated and non interpolated values data frames (one for each noPc meeting)
Df_int_1 = pd.DataFrame(columns = ['F19', 'F19_int'])
Df_int_1.iloc[:, 0] = Df_1.iloc[:, 1]
Df_int_1.iloc[:, 1] = Interp_1

Df_int_2 = pd.DataFrame(columns = ['K19', 'K19_int'])
Df_int_2.iloc[:, 0] = Df_2.iloc[:, 1]
Df_int_2.iloc[:, 1] = Interp_2

Df_int_3 = pd.DataFrame(columns = ['Q19', 'Q19_int'])
Df_int_3.iloc[:, 0] = Df_3.iloc[:, 1]
Df_int_3.iloc[:, 1] = Interp_3

Df_int_4 = pd.DataFrame(columns = ['V19', 'V19_int'])
Df_int_4.iloc[:, 0] = Df_4.iloc[:, 1]
Df_int_4.iloc[:, 1] = Interp_4

#Pcbias data frame
PCBiasLab = ['F19', 'K19', 'Q19', 'V19']
PCbias_1 = Df_int_1.iloc[:, 0] - Df_int_1.iloc[:, 1]
PCbias_2 = Df_int_2.iloc[:, 0] - Df_int_2.iloc[:, 1]
PCbias_3 = Df_int_3.iloc[:, 0] - Df_int_3.iloc[:, 1]
PCbias_4 = Df_int_4.iloc[:, 0] - Df_int_4.iloc[:, 1]

In [37]:
#Plot data
############################################################ 
Hike = PCBiasLab[0]

y_data = np.array(PCbias_1).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_1.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y',
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#0070C0'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################     
#initial Figure
figure10 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure10.title = ('Figure 6: ' + Hike + ' PcBias (abs) - ' + 
                  x_data[0].strftime('%Y-%m-%d') + 
                 ' to ' + 
                  x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure10.title_style = {'font-size': '13px'}
figure10.background_style = {'fill': 'white'}
    
figure10.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure10.layout.width = '45%'
figure10.layout.height = '380px'
figure10.layout.left = '30px'
figure10.legend_location = 'top-left'


############################################################  
############################################################  
############################################################  


#Plot data
############################################################
Hike = PCBiasLab[1]

y_data = np.array(PCbias_2).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_2.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y', 
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#DE2369'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################     
#initial Figure
figure11 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure11.title =  ('Figure 7: ' + Hike + ' PcBias (abs) - ' + 
                   x_data[0].strftime('%Y-%m-%d') + 
                  ' to ' + 
                   x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure11.title_style = {'font-size': '13px'}
figure11.background_style = {'fill': 'white'}
    
figure11.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure11.layout.width = '45%'
figure11.layout.height = '380px'
figure11.layout.left = '60px'
figure11.legend_location = 'top-left'


############################################################  
############################################################  
############################################################


#Plot data
############################################################ 
Hike = PCBiasLab[2]

y_data = np.array(PCbias_3).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_3.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y',
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#01B0F0'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 3: Figure (putting it all together)
############################################################     
#initial Figure
figure12 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure12.title = ('Figure 8: ' + Hike + ' PcBias (abs) - ' + 
                  x_data[0].strftime('%Y-%m-%d') + 
                 ' to ' + 
                  x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure12.title_style = {'font-size': '13px'}
figure12.background_style = {'fill': 'white'}
    
figure12.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure12.layout.width = '45%'
figure12.layout.height = '380px'
figure12.layout.left = '30px'
figure12.legend_location = 'top-left'


############################################################  
############################################################  
############################################################  


#Plot data
############################################################
Hike = PCBiasLab[3]

y_data = np.array(PCbias_4).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_4.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y', 
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#3CDBCC'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 3: Figure (putting it all together)
############################################################     
#initial Figure
figure13 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure13.title =  ('Figure 9: ' + Hike + ' PcBias (abs) - ' + 
                   x_data[0].strftime('%Y-%m-%d') + 
                  ' to ' + 
                   x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure13.title_style = {'font-size': '13px'}
figure13.background_style = {'fill': 'white'}
    
figure13.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure13.layout.width = '45%'
figure13.layout.height = '380px'
figure13.layout.left = '60px'
figure13.legend_location = 'top-left'

In [38]:
DesriptionBox_3 = widgets.HTML('<p> ' +
                               'For every NoPc meeting we compute the linear interpolation ' + 
                               'between the closest, adjacent, PC meetings (Example: for K19, we use H19 and M19). ' +
                               'The difference between the actual price and the interpolated price is what we call PcBias.' + 
                               '<br>' +
                               '2019 NoPc hikes were the first ones to show strong changes in PcBias with rate cuts becoming real, ' + 
                               'They had large vol and were difficult to trade:  ' +
                               '<br>' +
                               '<br>' +                               
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> During the hiking cycle, PcBias was negative and larger coming into expiration (F19, Dec18 Hike and K19 up to year end 2018)  </li>' +
                                       '<br>' + 
                                       '<li> PcBias took huge turns on the front when the meeting became live (Q19, after the May rally on May FOMC minutes), ' + 
                                       'even if the meeting was being consistently downplayed (V19, first week of Oct, bad econ data)  </li>' +
                                       '<br>' + 
                                       '<li>  Flat curve periods seem to present good opportunity trades to position for shocks (Q19 and K19, Jan to May), ' +
                                       'although arguable if we look at V19 </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_3.layout.width = '20%'
DesriptionBox_3.layout.height = '380px'
DesriptionBox_3.layout.left = '20px'
DesriptionBox_3.layout.top = '40px'
#DesriptionBox_2.layout.border = 'solid black'

In [39]:
VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2019 Hikes Press Conference Bias: </b>' + 
                   'Actual Price minus Interpolated Price (>0 means the hike should be lower) </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure10, figure11], layout = {'width': '100%'}), 
                               HBox([figure12, figure13], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_3]), BorderHtmlW])

In [40]:
#2020 Hikes set
#FFsDataList['Hikes_Specific_Data'].iloc[:, -20:].head()
HikeSet = ['Z19', 'F20', 'H20', 'J20', 'M20', 'N20', 'U20', 'V20', 'Z20']
Hikes2020 = FFsDataList['Hikes_Specific_Data'].loc[:, HikeSet]['2018':'2019']

#Reference for selection menu
NoPcRef = ['F20', 'J20', 'N20', 'V20']

#Start date
#StartD = '2018-10-3'
StartD = '2019-1-3'
StartD = '2018-11-08'

#2020 Cals set
PcCals = ['XF20', 'GJ20', 'KN20', 'QV20', 'XF21']
PcCals2020 = FFsDataList['Cal2M_Specific_Data'].loc[:, PcCals][StartD:]

NoPcCals = ['FG20', 'JK20', 'NQ20', 'VX20']
NoPcCals2020 = FFsDataList['Cal1M_Specific_Data'].loc[:, NoPcCals][StartD:]

#Data frames (one for each noPc meeting)
Df_0 = Hikes2020[StartD:]
Df_1 = Hikes2020[StartD:].loc[:, ('Z19', 'F20', 'H20')]
Df_2 = Hikes2020[StartD:].loc[:, ('H20', 'J20', 'M20')]
Df_3 = Hikes2020[StartD:].loc[:, ('M20', 'N20', 'U20')]
Df_4 = Hikes2020[StartD:].loc[:, ('U20', 'V20', 'Z20')]

#Interpolations (one for each noPc meeting)
Interp_1 = Df_1.iloc[:, 0] + ((Df_1.iloc[:, 1] - Df_1.iloc[:, 0]) / 2)
Interp_2 = Df_2.iloc[:, 0] + ((Df_2.iloc[:, 1] - Df_2.iloc[:, 0]) / 2)
Interp_3 = Df_3.iloc[:, 0] + ((Df_3.iloc[:, 1] - Df_3.iloc[:, 0]) / 2)
Interp_4 = Df_4.iloc[:, 0] + ((Df_4.iloc[:, 1] - Df_4.iloc[:, 0]) / 2)

#Interpolated and non interpolated values data frames (one for each noPc meeting)
Df_int_1 = pd.DataFrame(columns = ['F20', 'F20_int'])
Df_int_1.iloc[:, 0] = Df_1.iloc[:, 1]
Df_int_1.iloc[:, 1] = Interp_1

Df_int_2 = pd.DataFrame(columns = ['J20', 'J20_int'])
Df_int_2.iloc[:, 0] = Df_2.iloc[:, 1]
Df_int_2.iloc[:, 1] = Interp_2

Df_int_3 = pd.DataFrame(columns = ['N20', 'N20_int'])
Df_int_3.iloc[:, 0] = Df_3.iloc[:, 1]
Df_int_3.iloc[:, 1] = Interp_3

Df_int_4 = pd.DataFrame(columns = ['V20', 'V20_int'])
Df_int_4.iloc[:, 0] = Df_4.iloc[:, 1]
Df_int_4.iloc[:, 1] = Interp_4

#Pcbias data frame
PCbias_Df = pd.DataFrame(columns = ['F20', 'J20', 'N20', 'V20'])
PCbias_Df.iloc[:, 0] = Df_int_1.iloc[:, 0] - Df_int_1.iloc[:, 1]
PCbias_Df.iloc[:, 1] = Df_int_2.iloc[:, 0] - Df_int_2.iloc[:, 1]
PCbias_Df.iloc[:, 2] = Df_int_3.iloc[:, 0] - Df_int_3.iloc[:, 1]
PCbias_Df.iloc[:, 3] = Df_int_4.iloc[:, 0] - Df_int_4.iloc[:, 1]

In [41]:
#Hike spread tickers
PcNoPc = [Df_1.columns.tolist()[0] + Df_1.columns.tolist()[1], 
             Df_2.columns.tolist()[0] + Df_2.columns.tolist()[1],
             Df_3.columns.tolist()[0] + Df_3.columns.tolist()[1],
             Df_4.columns.tolist()[0] + Df_4.columns.tolist()[1]]

NoPcPc = [Df_1.columns.tolist()[1] + Df_1.columns.tolist()[2], 
             Df_2.columns.tolist()[1] + Df_2.columns.tolist()[2], 
             Df_3.columns.tolist()[1] + Df_3.columns.tolist()[2], 
             Df_4.columns.tolist()[1] + Df_4.columns.tolist()[2]]

#Flies tickers
PcNoPc_2 = [PcCals2020.columns.tolist()[i] + NoPcCals2020.columns.tolist()[i] for i in arange(0, 4)]
NoPcPc_2 = [NoPcCals2020.columns.tolist()[i] + PcCals2020.columns.tolist()[i + 1] for i in arange(0, 4)]

#Hike spread data frames
PcNoPc_Flies_Df = pd.DataFrame(columns = PcNoPc)
NoPcPc_Flies_Df = pd.DataFrame(columns = NoPcPc)

#Flies data frames
PcNoPc_CalFlies_Df = pd.DataFrame(columns = PcNoPc_2)
NoPcPc_CalFlies_Df = pd.DataFrame(columns = NoPcPc_2)

for i in arange(0, 4):
    
    if i == 0: CurrentDf = Df_1
    if i == 1: CurrentDf = Df_2
    if i == 2: CurrentDf = Df_3
    if i == 3: CurrentDf = Df_4        
    
    PcNoPc_Flies_Df.iloc[:, i] = (CurrentDf.iloc[:, 0] - CurrentDf.iloc[:, 1])/2
    NoPcPc_Flies_Df.iloc[:, i] = (CurrentDf.iloc[:, 1] - CurrentDf.iloc[:, 2])/2
    
    PcNoPc_CalFlies_Df.iloc[:, i] = (PcCals2020.iloc[:, i] - NoPcCals2020.iloc[:, i])/2
    NoPcPc_CalFlies_Df.iloc[:, i] = (NoPcCals2020.iloc[:, i] - PcCals2020.iloc[:, i + 1])/2

In [42]:
#Plot data
############################################################ 
Hike = PCbias_Df.columns.tolist()[0]

y_data = np.array(PCbias_Df.iloc[:, 0]).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_Df.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y',
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#0070C0'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################     
#initial Figure
figure6 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure6.title = ('Figure 10: ' + Hike + ' PcBias: ' + 
                  x_data[0].strftime('%Y-%m-%d') + 
                  ' to ' + 
                  x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure6.title_style = {'font-size': '13px'}
figure6.background_style = {'fill': 'white'}
    
figure6.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure6.layout.width = '45%'
figure6.layout.height = '380px'
figure6.layout.left = '30px'
figure6.legend_location = 'top-left'


############################################################  
############################################################  
############################################################  


#Plot data
############################################################
Hike = PCbias_Df.columns.tolist()[1]

y_data = np.array(PCbias_Df.iloc[:, 1]).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_Df.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y', 
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#DE2369'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 4: Figure (putting it all together)
############################################################     
#initial Figure
figure7 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure7.title = ('Figure 11: ' + Hike + ' PcBias: ' + 
                  x_data[0].strftime('%Y-%m-%d') + 
                  ' to ' + 
                  x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure7.title_style = {'font-size': '13px'}
figure7.background_style = {'fill': 'white'}
    
figure7.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure7.layout.width = '45%'
figure7.layout.height = '380px'
figure7.layout.left = '60px'
figure7.legend_location = 'top-left'


############################################################  
############################################################  
############################################################


#Plot data
############################################################ 
Hike = PCbias_Df.columns.tolist()[2]

y_data = np.array(PCbias_Df.iloc[:, 2]).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_Df.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y', 
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#01B0F0'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 3: Figure (putting it all together)
############################################################     
#initial Figure
figure8 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure8.title = ('Figure 12: ' + Hike + ' PcBias: ' + 
                  x_data[0].strftime('%Y-%m-%d') + 
                  ' to ' + 
                  x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure8.title_style = {'font-size': '13px'}
figure8.background_style = {'fill': 'white'}
    
figure8.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure8.layout.width = '45%'
figure8.layout.height = '380px'
figure8.layout.left = '30px'
figure8.legend_location = 'top-left'


############################################################  
############################################################  
############################################################  


#Plot data
############################################################
Hike = PCbias_Df.columns.tolist()[3]

y_data = np.array(PCbias_Df.iloc[:, 3]).transpose().astype('float')

#Indices (X tick labels, days to maturity)
x_data = PCbias_Df.index
############################################################

#Step 1: Scales & Axes
############################################################ 
#Scales 
MainTs_x_dates = DateScale()
MainTs_y_sc  = LinearScale() 

#X-Axis
MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                   tick_style = {'font-size': '12px'},
                   tick_format = '%d-%m-%y', 
                   num_ticks = 5,
                   label_location = 'end',
                   label = 'Date',
                   label_offset = '40px')

#Y-Axis
MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                   orientation = 'vertical', 
                   tick_format = '0.1f', 
                   tick_style = {'font-size': '12px'},
                   grid_color = '#EDEDED',
                   label_location = 'end',
                   label = 'PcBias (bps)',
                   label_offset = '40px')
############################################################    
 
#Step 2: Marks (plots)
############################################################
#Factors main time series 
TsPlot = Lines(x = x_data, 
               y = y_data, 
               labels = [Hike], 
               scales = {'x': MainTs_x_dates, 
                         'y' : MainTs_y_sc},
               colors = ['#3CDBCC'], 
               stroke_width = 1, 
               visible = True, 
               display_legend = True,
               marker = 'circle', marker_size = 20)
############################################################

#Step 3: Hover interaction
############################################################       
#Tooltip (main scatter)
def_tt = Tooltip(fields = ['x', 'y'], 
                 formats = ['%d/%m/%Y', '.2f'], 
                 labels = ['Date', 'PcBias (bps)'])

#Set the tooltip interaction(s)
TsPlot.tooltip = def_tt
TsPlot.interactions = {'hover': 'tooltip'}
############################################################

#Step 3: Figure (putting it all together)
############################################################     
#initial Figure
figure9 = Figure(marks = [TsPlot], 
                 axes = [MainTs_x_ax, MainTs_y_ax])

#Figure Title
figure9.title =  ('Figure 13: ' + Hike + ' PcBias: ' + 
                  x_data[0].strftime('%Y-%m-%d') + 
                  ' to ' + 
                  x_data[-1].strftime('%Y-%m-%d'))

#Figure layout (except size attributes, defined on section 4)
figure9.title_style = {'font-size': '13px'}
figure9.background_style = {'fill': 'white'}
    
figure9.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
figure9.layout.width = '45%'
figure9.layout.height = '380px'
figure9.layout.left = '60px'
figure9.legend_location = 'top-left'

In [43]:
DesriptionBox_4 = widgets.HTML('<p>' + 
                               '2020 NoPc hikes were also altered by the curve flattening to price cuts, ' + 
                               'They had a more manageable vol and were easier to trade, praticularly from J20 forward:  ' +
                               '<br>' +
                               '<br>' +                               
                                   '<ul style = "color: #125CB2; font-size: 16px; font-weight: bold;">' + 
                                       '<li> With cuts priced in, the PcBias was positive and larger coming into expiration (F20 and J20, first half of 2019) </li>' +
                                        '<br>' +   
                                       '<li> F20 and J20 PcBias grew as the curve rolled until the May FOMC minutes crash, when Q19 ' +
                                       'became a live meeting. After that, the PcBias became more stable (smoother curve) </li>' +
                                       '<br>' + 
                                       '<li> The curve was flatter on the back, that meant a closer to 0 and more mean reverting PcBias (N20 & V20) </li>' +
                                       '<br>' + 
                                   '</ul>' + 
                               '</p>')

DesriptionBox_4.layout.width = '20%'
DesriptionBox_4.layout.height = '380px'
DesriptionBox_4.layout.left = '20px'
DesriptionBox_4.layout.top = '40px'

In [44]:
VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 Hikes Press Conference Bias: </b>' + 
                   'Actual Price minus Interpolated Price (>0 means the hike should be lower) </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure6, figure7], layout = {'width': '100%'}), 
                               HBox([figure8, figure9], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_4]), BorderHtmlW])

In [45]:
def FliesMiniPanel(Strategy, RollingWindow):

    #Selection data
    ############################################################ 
    #Current selected hike
    SelHike = HikeSet.index(Strategy)
    SelHike_1 = NoPcRef.index(Strategy)
    ############################################################ 


    #Plot data
    ############################################################ 
    Hike = HikeSet[SelHike - 1:(SelHike + 2)]

    y_data = np.array(Df_0.iloc[:, 
            (SelHike - 1, SelHike, SelHike + 1)]).transpose().astype('float')

    #Indices (X tick labels, days to maturity)
    x_data = Df_0.index
    ############################################################

    #Step 1: Scales & Axes
    ############################################################ 
    #Scales 
    MainTs_x_dates = DateScale()
    MainTs_y_sc  = LinearScale() 

    #X-Axis
    MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                       tick_style = {'font-size': '12px'},
                       tick_format = '%d-%m-%y',
                       num_ticks = 10,
                       label_location = 'end',
                       label = 'Date',
                       label_offset = '40px')

    #Y-Axis
    MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                       orientation = 'vertical', 
                       tick_format = '0.1f', 
                       tick_style = {'font-size': '12px'},
                       grid_color = '#EDEDED',
                       label_location = 'end',
                       label = 'Price (bps)',
                       label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Factors main time series 
    TsPlot = Lines(x = x_data, 
                   y = y_data, 
                   labels = Hike, 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#F53F52', '#0070C0', '#3CDBCC'], 
                   stroke_width = 1, 
                   visible = True, 
                   display_legend = True,
                   marker = 'circle', marker_size = 15)
    ############################################################

    #Step 3: Hover interaction
    ############################################################       
    #Tooltip (main scatter)
    def_tt = Tooltip(fields = ['x', 'y'], 
                     formats = ['%d/%m/%Y', '.2f'], 
                     labels = ['Date', 'PcBias (bps)'])

    #Set the tooltip interaction(s)
    TsPlot.tooltip = def_tt
    TsPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################     
    #initial Figure
    figure14 = Figure(marks = [TsPlot], 
                     axes = [MainTs_x_ax, MainTs_y_ax])

    #Figure Title
    figure14.title = (Strategy + ' (Hike) plus Adjacent Meetings Time Series: ' + 
                      x_data[0].strftime('%Y-%m-%d') + 
                     ' to ' + 
                      x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure14.title_style = {'font-size': '13px'}
    figure14.background_style = {'fill': 'white'}

    figure14.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
    figure14.layout.width = '93%'
    figure14.layout.height = '380px'
    figure14.layout.left = '30px'
    figure14.legend_location = 'top-right'
    ############################################################
    
    #Step 3 II: Brush interaction
    ############################################################    
    #Create Brush selector  
    Mult_intsel_temp = MultiSelector(
                     scale = MainTs_x_dates, 
                     marks = [TsPlot],
                     color = '#FCCCDD')

    #Link brush selector to figure instance
    #figure14.interaction = Mult_intsel_temp


    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################ 
    Hike = [PcNoPc_CalFlies_Df.columns.tolist()[SelHike_1]]

    y_data = np.array(PcNoPc_CalFlies_Df.iloc[:, SelHike_1]).transpose().astype('float')

    #Indices (X tick labels, days to maturity)
    x_data = PcNoPc_CalFlies_Df.index
    ############################################################

    #Step 1: Scales & Axes
    ############################################################ 
    #Scales 
    MainTs_x_dates = DateScale()
    MainTs_y_sc  = LinearScale() 

    #X-Axis
    MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                       tick_style = {'font-size': '12px'},
                       tick_format = '%d-%m-%y',
                       num_ticks = 5,
                       label_location = 'end',
                       label = 'Date',
                       label_offset = '40px')

    #Y-Axis
    MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                       orientation = 'vertical', 
                       tick_format = '0.1f', 
                       tick_style = {'font-size': '12px'},
                       grid_color = '#EDEDED',
                       label_location = 'end',
                       label = 'Price (bps)',
                       label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Factors main time series 
    TsPlot = Lines(x = x_data, 
                   y = y_data, 
                   labels = Hike, 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#0070C0'], 
                   stroke_width = 1, 
                   visible = True, 
                   display_legend = True,
                   marker = 'circle', marker_size = 15)
    ############################################################

    #Step 3: Hover interaction
    ############################################################       
    #Tooltip (main scatter)
    def_tt = Tooltip(fields = ['x', 'y'], 
                     formats = ['%d/%m/%Y', '.2f'], 
                     labels = ['Date', 'PcBias (bps)'])

    #Set the tooltip interaction(s)
    TsPlot.tooltip = def_tt
    TsPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################     
    #initial Figure
    figure15 = Figure(marks = [TsPlot], 
                     axes = [MainTs_x_ax, MainTs_y_ax])

    #Figure Title
    figure15.title = (Hike[0] + ' Cal Spread Time Series: ' + 
                      x_data[0].strftime('%Y-%m-%d') + 
                     ' to ' + 
                      x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure15.title_style = {'font-size': '13px'}
    figure15.background_style = {'fill': 'white'}

    figure15.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
    figure15.layout.width = '45%'
    figure15.layout.height = '380px'
    figure15.layout.left = '30px'
    figure15.legend_location = 'top-right'    
    ############################################################
    
    #Step 3 II: Brush interaction
    ############################################################    
    #Link brush selector to figure instance
    #figure15.interaction = Mult_intsel_temp    


    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################ 
    Hike = [NoPcPc_CalFlies_Df.columns.tolist()[SelHike_1]]

    y_data = np.array(NoPcPc_CalFlies_Df.iloc[:, SelHike_1]).transpose().astype('float')

    #Indices (X tick labels, days to maturity)
    x_data = NoPcPc_CalFlies_Df.index
    ############################################################

    #Step 1: Scales & Axes
    ############################################################ 
    #Scales 
    MainTs_x_dates = DateScale()
    MainTs_y_sc  = LinearScale() 

    #X-Axis
    MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                       tick_style = {'font-size': '12px'},
                       tick_format = '%d-%m-%y',
                       num_ticks = 5,
                       label_location = 'end',
                       label = 'Date',
                       label_offset = '40px')

    #Y-Axis
    MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                       orientation = 'vertical', 
                       tick_format = '0.1f', 
                       tick_style = {'font-size': '12px'},
                       grid_color = '#EDEDED',
                       label_location = 'end',
                       label = 'Price (bps)',
                       label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Factors main time series 
    TsPlot = Lines(x = x_data, 
                   y = y_data, 
                   labels = Hike, 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#3CDBCC'], 
                   stroke_width = 1, 
                   visible = True, 
                   display_legend = True,
                   marker = 'circle', marker_size = 15)
    ############################################################

    #Step 3: Hover interaction
    ############################################################       
    #Tooltip (main scatter)
    def_tt = Tooltip(fields = ['x', 'y'], 
                     formats = ['%d/%m/%Y', '.2f'], 
                     labels = ['Date', 'PcBias (bps)'])

    #Set the tooltip interaction(s)
    TsPlot.tooltip = def_tt
    TsPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################     
    #initial Figure
    figure16 = Figure(marks = [TsPlot], 
                     axes = [MainTs_x_ax, MainTs_y_ax])

    #Figure Title
    figure16.title = (Hike[0] + ' Cal Spread Time Series: ' + 
                      x_data[0].strftime('%Y-%m-%d') + 
                     ' to ' + 
                      x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure16.title_style = {'font-size': '13px'}
    figure16.background_style = {'fill': 'white'}

    figure16.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
    figure16.layout.width = '45%'
    figure16.layout.height = '380px'
    figure16.layout.left = '60px'
    figure16.legend_location = 'top-right'
    ############################################################
    
    #Step 3 II: Brush interaction
    ############################################################    
    #Link brush selector to figure instance
    #figure16.interaction = Mult_intsel_temp  

    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################
    Hike = [PcNoPc_CalFlies_Df.columns.tolist()[SelHike_1]]
    y_data = np.array(PcNoPc_CalFlies_Df.iloc[:, SelHike_1]).transpose().astype('float')
    ############################################################

    #Step 1: Scales & Axes
    ############################################################     
    #Scales
    Hist_x = LinearScale()
    Hist_y = LinearScale()

    #X-Axis
    Hist_ax_x = Axis(scale = Hist_x, 
                     tick_format = '.2f', 
                     tick_style = {'font-size': '12px'},
                     label_location = 'end',
                     label = 'Price (bps)',
                     label_offset = '40px')

    #Y-Axis
    Hist_ax_y = Axis(scale = Hist_y, 
                     orientation = 'vertical', 
                     tick_format = '0f',     
                     tick_style = {'font-size': '12px'}, 
                     grid_color = '#EDEDED',
                     label_location = 'middle',
                     label = 'Count',
                     label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Histogram plot (price)
    HistPlot = Hist(sample = y_data, 
                    normalized =  False,
                    scales = {'sample': Hist_x, 
                              'count': Hist_y}, 
                    padding = 0.25, 
                    bins = 10,
                    colors = ['#0070C0'], 
                    stroke = '#D8D8D8',
                    labels = Hike,
                    display_legend = True)    

    #Setting the tick values to be the mid points of the bins
    Hist_ax_x.tick_values = HistPlot.midpoints

    #Setting histogram bar opacities 
    HistPlot.opacities = [0.3] * HistPlot.bins
    ############################################################    

    #Step 3: Hover interaction
    ############################################################      
    #Creating the tooltip
    def_tt = Tooltip(fields = ['count', 'midpoint'], 
             formats = ['', '.2f'], 
             labels = ['Count', 'Midpoint'])

    #Set up the tooltip interaction (price)
    HistPlot.tooltip = def_tt
    HistPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################         
    #initial Figure
    figure17 = Figure(marks = [HistPlot], 
                     axes = [Hist_ax_x, Hist_ax_y])

    #Figure Title
    figure17.title =  (Hike[0] + ' Cal Spread Distr Data: ' + 
                      x_data[0].strftime('%Y-%m-%d') + 
                     ' to ' + 
                      x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure17.title_style = {'font-size': '13px'}
    figure17.background_style = {'fill': 'white'} 

    figure17.fig_margin = {'top':40, 'bottom':50, 'left':60, 'right':20}
    figure17.layout.width = '45%'
    figure17.layout.left = '30px'
    figure17.layout.height = '380px'
    figure17.legend_location = 'top-left'


    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################
    Hike = [NoPcPc_CalFlies_Df.columns.tolist()[SelHike_1]]
    y_data = np.array(NoPcPc_CalFlies_Df.iloc[:, SelHike_1]).transpose().astype('float')
    ############################################################

    #Step 1: Scales & Axes
    ############################################################     
    #Scales
    Hist_x = LinearScale()
    Hist_y = LinearScale()

    #X-Axis
    Hist_ax_x = Axis(scale = Hist_x, 
                     tick_format = '.2f', 
                     tick_style = {'font-size': '12px'},
                     label_location = 'end',
                     label = 'Price (bps)',
                     label_offset = '40px')

    #Y-Axis
    Hist_ax_y = Axis(scale = Hist_y, 
                     orientation = 'vertical', 
                     tick_format = '0f',     
                     tick_style = {'font-size': '12px'}, 
                     grid_color = '#EDEDED',
                     label_location = 'middle',
                     label = 'Count',
                     label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Histogram plot (price)
    HistPlot = Hist(sample = y_data, 
                    normalized =  False,
                    scales = {'sample': Hist_x, 
                              'count': Hist_y}, 
                    padding = 0.25, 
                    bins = 10,
                    colors = ['#3CDBCC'], 
                    stroke = '#D8D8D8',
                    labels = Hike,
                    display_legend = True)    

    #Setting the tick values to be the mid points of the bins
    Hist_ax_x.tick_values = HistPlot.midpoints

    #Setting histogram bar opacities 
    HistPlot.opacities = [0.3] * HistPlot.bins
    ############################################################    

    #Step 3: Hover interaction
    ############################################################      
    #Creating the tooltip
    def_tt = Tooltip(fields = ['count', 'midpoint'], 
             formats = ['', '.2f'], 
             labels = ['Count', 'Midpoint'])

    #Set up the tooltip interaction (price)
    HistPlot.tooltip = def_tt
    HistPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################         
    #initial Figure
    figure18 = Figure(marks = [HistPlot], 
                     axes = [Hist_ax_x, Hist_ax_y])

    #Figure Title
    figure18.title =   (Hike[0] + ' Cal Spread Distr Data: ' + 
                      x_data[0].strftime('%Y-%m-%d') + 
                     ' to ' + 
                      x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure18.title_style = {'font-size': '13px'}
    figure18.background_style = {'fill': 'white'} 

    figure18.fig_margin = {'top':40, 'bottom':50, 'left':60, 'right':20}
    figure18.layout.width = '45%'
    figure18.layout.left = '60px'
    figure18.layout.height = '380px'
    figure18.legend_location = 'top-left'


    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################
    Labels = [PcCals2020.columns.tolist()[SelHike_1], 
              NoPcCals2020.columns.tolist()[SelHike_1]]

    y_data = np.array(PcCals2020.iloc[:, SelHike_1].diff()).transpose().astype('float')
    y2_data = np.array(NoPcCals2020.iloc[:, SelHike_1].diff()).transpose().astype('float')
    ############################################################

    #Step 1: Scales & Axes
    ############################################################     
    #Scales
    Hist_x = LinearScale()
    Hist_y = LinearScale()

    #X-Axis
    Hist_ax_x = Axis(scale = Hist_x, 
                     tick_format = '.2f', 
                     tick_style = {'font-size': '12px'},
                     label_location = 'end',
                     label = 'Net Change (bps)',
                     label_offset = '40px')

    #Y-Axis
    Hist_ax_y = Axis(scale = Hist_y, 
                     orientation = 'vertical', 
                     tick_format = '0f',     
                     tick_style = {'font-size': '12px'}, 
                     grid_color = '#EDEDED',
                     label_location = 'middle',
                     label = 'Count',
                     label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Histogram plot (price)
    HistPlot = Hist(sample = y_data, 
                    normalized =  False,
                    scales = {'sample': Hist_x, 
                              'count': Hist_y}, 
                    padding = 0.25, 
                    bins = 10,
                    colors = ['#01B0F0'], 
                    stroke = '#D8D8D8',
                    labels = [Labels[0]],
                    display_legend = True)    

    #Setting the tick values to be the mid points of the bins
    Hist_ax_x.tick_values = HistPlot.midpoints

    #Setting histogram bar opacities 
    HistPlot.opacities = [0.4] * HistPlot.bins


    #Histogram plot (price)
    HistPlot2 = Hist(sample = y2_data, 
                    normalized =  False,
                    scales = {'sample': Hist_x, 
                              'count': Hist_y}, 
                    padding = 0.25, 
                    bins = 10,
                    colors = ['#DE2369'], 
                    stroke = '#D8D8D8',
                    labels = [Labels[1]],
                    display_legend = True)    

    #Setting histogram bar opacities 
    HistPlot2.opacities = [0.4] * HistPlot2.bins
    ############################################################    

    #Step 3: Hover interaction
    ############################################################      
    #Creating the tooltip
    def_tt = Tooltip(fields = ['count', 'midpoint'], 
             formats = ['', '.2f'], 
             labels = ['Count', 'Midpoint'])

    #Set up the tooltip interaction (price)
    HistPlot.tooltip = def_tt
    HistPlot.interactions = {'hover': 'tooltip'}

    #Set up the tooltip interaction (price)
    HistPlot2.tooltip = def_tt
    HistPlot2.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################         
    #initial Figure
    figure19 = Figure(marks = [HistPlot, HistPlot2], 
                     axes = [Hist_ax_x, Hist_ax_y])

    #Figure Title
    figure19.title =  (Labels[0] + ' & ' + Labels[1] + 
                       ' Daily Net Change Distr Data: ' + 
                       x_data[0].strftime('%Y-%m-%d') + 
                       ' to ' + 
                       x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure19.title_style = {'font-size': '13px'}
    figure19.background_style = {'fill': 'white'} 

    figure19.fig_margin = {'top':40, 'bottom':50, 'left':60, 'right':20}
    figure19.layout.width = '45%'
    figure19.layout.left = '30px'
    figure19.layout.height = '380px'
    figure19.legend_location = 'top-left'


    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################
    Labels = [NoPcCals2020.columns.tolist()[SelHike_1], PcCals2020.columns.tolist()[SelHike_1 + 1]]

    y_data = np.array(NoPcCals2020.iloc[:, SelHike_1].diff()).transpose().astype('float')
    y2_data = np.array(PcCals2020.iloc[:, SelHike_1 + 1].diff()).transpose().astype('float')
    ############################################################

    #Step 1: Scales & Axes
    ############################################################     
    #Scales
    Hist_x = LinearScale()
    Hist_y = LinearScale()

    #X-Axis
    Hist_ax_x = Axis(scale = Hist_x, 
                     tick_format = '.2f', 
                     tick_style = {'font-size': '12px'},
                     label_location = 'end',
                     label = 'Net Change (bps)',
                     label_offset = '40px')

    #Y-Axis
    Hist_ax_y = Axis(scale = Hist_y, 
                     orientation = 'vertical', 
                     tick_format = '0f',     
                     tick_style = {'font-size': '12px'}, 
                     grid_color = '#EDEDED',
                     label_location = 'middle',
                     label = 'Count',
                     label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Histogram plot (price)
    HistPlot = Hist(sample = y_data, 
                    normalized =  False,
                    scales = {'sample': Hist_x, 
                              'count': Hist_y}, 
                    padding = 0.25, 
                    bins = 10,
                    colors = ['#01B0F0'], 
                    stroke = '#D8D8D8',
                    labels = [Labels[0]],
                    display_legend = True)    

    #Setting the tick values to be the mid points of the bins
    Hist_ax_x.tick_values = HistPlot.midpoints

    #Setting histogram bar opacities 
    HistPlot.opacities = [0.4] * HistPlot.bins


    #Histogram plot (price)
    HistPlot2 = Hist(sample = y2_data, 
                    normalized =  False,
                    scales = {'sample': Hist_x, 
                              'count': Hist_y}, 
                    padding = 0.25, 
                    bins = 10,
                    colors = ['#DE2369'], 
                    stroke = '#D8D8D8',
                    labels = [Labels[1]],
                    display_legend = True)    

    #Setting histogram bar opacities 
    HistPlot2.opacities = [0.4] * HistPlot2.bins
    ############################################################    

    #Step 3: Hover interaction
    ############################################################      
    #Creating the tooltip
    def_tt = Tooltip(fields = ['count', 'midpoint'], 
             formats = ['', '.2f'], 
             labels = ['Count', 'Midpoint'])

    #Set up the tooltip interaction (price)
    HistPlot.tooltip = def_tt
    HistPlot.interactions = {'hover': 'tooltip'}

    #Set up the tooltip interaction (price)
    HistPlot2.tooltip = def_tt
    HistPlot2.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################         
    #initial Figure
    figure20 = Figure(marks = [HistPlot, HistPlot2], 
                     axes = [Hist_ax_x, Hist_ax_y])

    #Figure Title
    figure20.title =   (Labels[0] + ' & ' + Labels[1] + 
                       ' Daily Net Change Distr Data: ' + 
                       x_data[0].strftime('%Y-%m-%d') + 
                       ' to ' + 
                       x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure20.title_style = {'font-size': '13px'}
    figure20.background_style = {'fill': 'white'} 

    figure20.fig_margin = {'top':40, 'bottom':50, 'left':60, 'right':20}
    figure20.layout.width = '45%'
    figure20.layout.left = '60px'
    figure20.layout.height = '380px'
    figure20.legend_location = 'top-left'


    ############################################################  
    ############################################################  
    ############################################################ 


    #Plot data
    ############################################################ 
    Labels = [PcCals2020.columns.tolist()[SelHike_1], NoPcCals2020.columns.tolist()[SelHike_1]]

    Rolling_1 = PcCals2020.iloc[:, SelHike_1].diff().rolling(RollingWindow).std()
    Rolling_2 = NoPcCals2020.iloc[:, SelHike_1].diff().rolling(RollingWindow).std()
    RollingShare_leg_1 = Rolling_1 / (Rolling_1 + Rolling_2)


    y_data = np.array([np.array(RollingShare_leg_1).transpose().astype('float'), 
                       np.repeat(0, len(RollingShare_leg_1))])

    y_data2 = np.array([np.array(RollingShare_leg_1).transpose().astype('float'), 
                       np.repeat(1, len(RollingShare_leg_1))])

    #Indices (X tick labels, days to maturity)
    x_data = RollingShare_leg_1.index
    ############################################################

    #Step 1: Scales & Axes
    ############################################################ 
    #Scales 
    MainTs_x_dates = DateScale()
    MainTs_y_sc  = LinearScale() 

    #X-Axis
    MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                       tick_style = {'font-size': '12px'},
                       tick_format = '%d-%m-%y',
                       num_ticks = 5,
                       label_location = 'end',
                       label = 'Date',
                       label_offset = '40px')

    #Y-Axis
    MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                       orientation = 'vertical', 
                       tick_format = '0.1f', 
                       tick_style = {'font-size': '12px'},
                       grid_color = '#EDEDED',
                       label_location = 'end',
                       label = 'Share of Total Variance',
                       label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Factors main time series 
    TsPlot = Lines(x = x_data, 
                   y = y_data, 
                   labels = [], 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#3CDBCC'], 
                   stroke_width = 1, 
                   visible = True, 
                   fill = 'between',
                   fill_opacities = [0.5],                
                   display_legend = False,
                   marker = 'circle', marker_size = 0)

    TsPlot2 = Lines(x = x_data, 
                   y = y_data2, 
                   labels = [], 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#DE2369'], 
                   stroke_width = 1, 
                   visible = True, 
                   fill = 'between',
                   fill_opacities = [0.5], 
                   display_legend = False,
                   marker = 'circle', marker_size = 0)

    LabelsPlot = Label(x = [0.3, 0.3], y = [0.06, 0.90], 
                       text = [Labels[0] + ' Share of Total Vol (Std)', 
                               Labels[1] + ' Share of Total Vol (Std)'], 
                       default_size = 16, font_weight = 'bolder', 
                       colors = ['#0070C0', '#0070C0'], 
                       enable_move = True) 
    ############################################################

    #Step 3: Hover interaction
    ############################################################       
    #Tooltip (main scatter)
    def_tt = Tooltip(fields = ['x', 'y'], 
                     formats = ['%d/%m/%Y', '.2f'], 
                     labels = ['Date', 'PcBias (bps)'])

    #Set the tooltip interaction(s)
    TsPlot.tooltip = def_tt
    TsPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################     
    #initial Figure
    figure21 = Figure(marks = [TsPlot, TsPlot2, LabelsPlot], 
                     axes = [MainTs_x_ax, MainTs_y_ax])

    #Figure Title
    figure21.title = (Labels[0] + ' & ' + Labels[1] + 
                       ' Share of Volatility (Rolling Std): ' + 
                       x_data[0].strftime('%Y-%m-%d') + 
                       ' to ' + 
                       x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure21.title_style = {'font-size': '13px'}
    figure21.background_style = {'fill': 'white'}

    figure21.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
    figure21.layout.width = '45%'
    figure21.layout.height = '380px'
    figure21.layout.left = '30px'
    figure21.legend_location = 'top-right'


    ############################################################  
    ############################################################  
    ############################################################  


    #Plot data
    ############################################################ 
    Labels = [PcCals2020.columns.tolist()[SelHike_1 + 1], NoPcCals2020.columns.tolist()[SelHike_1]]

    Rolling_1 = PcCals2020.iloc[:, SelHike_1 + 1].diff().rolling(RollingWindow).std()
    Rolling_2 = NoPcCals2020.iloc[:, SelHike_1].diff().rolling(RollingWindow).std()
    RollingShare_leg_1 = Rolling_1 / (Rolling_1 + Rolling_2)


    y_data = np.array([np.array(RollingShare_leg_1).transpose().astype('float'), 
                       np.repeat(0, len(RollingShare_leg_1))])

    y_data2 = np.array([np.array(RollingShare_leg_1).transpose().astype('float'), 
                       np.repeat(1, len(RollingShare_leg_1))])

    #Indices (X tick labels, days to maturity)
    x_data = RollingShare_leg_1.index
    ############################################################

    #Step 1: Scales & Axes
    ############################################################ 
    #Scales 
    MainTs_x_dates = DateScale()
    MainTs_y_sc  = LinearScale() 

    #X-Axis
    MainTs_x_ax = Axis(scale = MainTs_x_dates, 
                       tick_style = {'font-size': '12px'},
                       tick_format = '%d-%m-%y',
                       num_ticks = 5,
                       label_location = 'end',
                       label = 'Date',
                       label_offset = '40px')

    #Y-Axis
    MainTs_y_ax = Axis(scale = MainTs_y_sc, 
                       orientation = 'vertical', 
                       tick_format = '0.1f', 
                       tick_style = {'font-size': '12px'},
                       grid_color = '#EDEDED',
                       label_location = 'end',
                       label = 'Share of Total Variance',
                       label_offset = '40px')
    ############################################################    

    #Step 2: Marks (plots)
    ############################################################
    #Factors main time series 
    TsPlot = Lines(x = x_data, 
                   y = y_data, 
                   labels = [], 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#3CDBCC'], 
                   stroke_width = 1, 
                   visible = True, 
                   fill = 'between',
                   fill_opacities = [0.5],                
                   display_legend = False,
                   marker = 'circle', marker_size = 0)

    TsPlot2 = Lines(x = x_data, 
                   y = y_data2, 
                   labels = [], 
                   scales = {'x': MainTs_x_dates, 
                             'y' : MainTs_y_sc},
                   colors = ['#DE2369'], 
                   stroke_width = 1, 
                   visible = True, 
                   fill = 'between',
                   fill_opacities = [0.5], 
                   display_legend = False,
                   marker = 'circle', marker_size = 0)

    LabelsPlot = Label(x = [0.3, 0.3], y = [0.06, 0.90],
                       text = [Labels[0] + ' Share of Total Vol (Std)', 
                               Labels[1] + ' Share of Total Vol (Std)'], 
                       default_size = 16, font_weight = 'bolder', 
                       colors = ['#0070C0', '#0070C0'], 
                       enable_move = True) 
    ############################################################

    #Step 3: Hover interaction
    ############################################################       
    #Tooltip (main scatter)
    def_tt = Tooltip(fields = ['x', 'y'], 
                     formats = ['%d/%m/%Y', '.2f'], 
                     labels = ['Date', 'PcBias (bps)'])

    #Set the tooltip interaction(s)
    TsPlot.tooltip = def_tt
    TsPlot.interactions = {'hover': 'tooltip'}
    ############################################################

    #Step 4: Figure (putting it all together)
    ############################################################     
    #initial Figure
    figure22 = Figure(marks = [TsPlot, TsPlot2, LabelsPlot], 
                     axes = [MainTs_x_ax, MainTs_y_ax])

    #Figure Title
    figure22.title = (Labels[0] + ' & ' + Labels[1] + 
                       ' Share of Volatility (Rolling Std): ' + 
                       x_data[0].strftime('%Y-%m-%d') + 
                       ' to ' + 
                       x_data[-1].strftime('%Y-%m-%d'))

    #Figure layout (except size attributes, defined on section 4)
    figure22.title_style = {'font-size': '13px'}
    figure22.background_style = {'fill': 'white'}

    figure22.fig_margin = {'top':40, 'bottom':50, 'left':80, 'right':20}
    figure22.layout.width = '45%'
    figure22.layout.height = '380px'
    figure22.layout.left = '60px'
    figure22.legend_location = 'top-right'
    
    return(figure14, figure15, figure16, figure17, figure18, 
           figure19, figure20, figure21, figure22)

In [46]:
(figure14_1, figure15_1, figure16_1, figure17_1, figure18_1, 
           figure19_1, figure20_1, figure21_1, figure22_1) = FliesMiniPanel('F20', 40)


DesriptionBox_5 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> Flat curve on the first 2 months of 2019 meant Dec19 and Jan20 were close. ' + 
                                       'With the March and May rallies, Dec19 moved ahead of Jan20 and the fly XFG0 moved consistently down. ' +
                                       '<br>' + 
                                       'By the end of June, with Aug19 being priced as the first cut, the fly XFG0 stabilized, but the bias remained (XFG0 < 0) </li>' +
                                       '<br>' +   
                                       '<li> Jan20 and Mar20 behaved similarly most of the year until the May FOMC minutes crash (end of May), when Aug19 ' +
                                       'became a likely rate cut. After that, the spread widened, and Jan20 started moving closer to Dec19. ' +
                                       '<br>' +
                                       'The fly FGJ0 was stable close to 0 and quickly moved below, the August rally on trump tweets ' +
                                       'and the actual rate cut pushed the fly even lower.  </li>' +
                                       '<br>' + 
                                       '<li> FGJ0 (Jan20-Mar20) displayed less direction than XFG0 (Dec19-Jan20), the FGJ0 fly trading close or above 0 ' +
                                       'was a pretty comfortable short in favor of any strong rally, all year. The september selloff caused a big rebound ' +
                                       'that opened up the possibility for new shorts sucessfully </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_5.layout.width = '23%'
DesriptionBox_5.layout.height = '380px'
DesriptionBox_5.layout.left = '-20px'
DesriptionBox_5.layout.top = '40px'

VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'Jan20 (F20) hike time series and XFG0 / FGJ0 flies </p>'),
      BorderHtmlW, HBox([VBox([figure14_1, 
                               HBox([figure15_1, figure16_1], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_5]), BorderHtmlW])

In [47]:
DesriptionBox_6 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> For XFG0, the daily behaviour of both legs was not the same, we can see the XF20 calendar NC distribution ' + 
                                       'has fatter tails (specially on the negative NC side), and that the fly had a bigger share of its volatility coming from the first leg (XF20 cal). ' +
                                       '<br>' + 
                                       'That means the fly had a larger market exposure than the second one, due to its persistent Bias in favor of Dec19 </li>' +
                                       '<br>' +   
                                       '<li> FGJ0 had a much more consistent behaviour, both legs have similar daily NC distributions, and as the year progressed, ' +
                                       'the fly had a larger share of its volatility explained by the the first leg (NoPc meeting, FG20 calendar), but closer to 50%, ' +
                                       'until the september selloff  </li>' +
                                       '<br>' + 
                                       '<li> So more market exposure on the first fly (Pc-NoPc structure), but likely better roldown. The second fly (NoPc-Pc structure) ' +
                                       'was more stable for trading and until the september selloff was pretty consistent in terms of its legs behaviour </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_6.layout.width = '23%'
DesriptionBox_6.layout.height = '380px'
DesriptionBox_6.layout.left = '-20px'
DesriptionBox_6.layout.top = '40px'


VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'XFG0 / FGJ0 flies leg NC distribution and leg volatility (40 day rolling Std) </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure19_1, figure20_1], layout = {'width': '100%'}), 
                               HBox([figure21_1, figure22_1], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_6]), BorderHtmlW])

In [48]:
(figure14_2, figure15_2, figure16_2, figure17_2, figure18_2, 
           figure19_2, figure20_2, figure21_2, figure22_2) = FliesMiniPanel('J20', 40)

DesriptionBox_7 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> The first fly presented a stronger bias ' + 
                                       'in favor of the PC meeting. GJK0 was very directional on the first three rallys (Dec18, Mar and May19),  ' + 
                                       'consistently moving down until the end of June (Aug19 became live). ' +
                                       'The fly stabilized then, but the bias remained as the curve had a positive slope with cuts. </li>' +
                                       '<br>' +   
                                       '<li>  While the previous spread (FGJ0) traded for the most part below zero as F20 trailed behind Z19, ' +
                                       ' Apr20 and Jun20 behaved differently (flatter and smoother curve on this section). ' +
                                       '<br>' +
                                       'The fly JKN0 was consistently biased above 0, with Apr20 being normally above Jun20 and stable throughout March and May rallies, and ' +
                                       ' adjusting by the end of June (Aug19 became live) and on the August rally </li>' +
                                       '<br>' + 
                                       '<li> JKN0 (Apr20-Jun20) displayed less direction than GJK0 (Mar19-Apr20). JKN0 consistently traded above 0, ' +
                                       'which made it a pretty good potential short to capitalize on strong rallies plus its rolldown. ' +
                                       'Both with the Sept and Oct selloffs the fly moved back up but not to the levels we saw back in mid 2019 </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_7.layout.width = '23%'
DesriptionBox_7.layout.height = '380px'
DesriptionBox_7.layout.left = '-20px'
DesriptionBox_7.layout.top = '40px'


VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'Apr20 (J20) hike time series and GJK0 / JKN0 flies </p>'),
      BorderHtmlW, HBox([VBox([figure14_2, 
                               HBox([figure15_2, figure16_2], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_7]), BorderHtmlW])

In [49]:
DesriptionBox_8 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> For GJK0, we have once more different daily NC behaviour for both legs (as for XFG0). The Pc leg (GJ20 calendar)  ' + 
                                       ' has fatter tails on the negative NC side of its daily NC distribution. ' +
                                       '<br>' + 
                                       'As for the share of its volatility explained by the first leg (GJ20 cal), the bias was smaller than for the previous fly (XFG0), '+
                                       'but consistently above 60% until the end of June.</li>' +
                                       '<br>' +   
                                       '<li> JKN0 was more consistent on its daily leg NC distributions, both legs were similar in that regard. ' +
                                       'But same as GJK0, the fly had a larger (above 60%) share of its volatility explained by the the PC leg (the second leg in this case, the KN20 cal) ' +
                                       'until the september selloff. This was likely due to how stable the JK20 calendar (Apr20 meeting) was throughout the year  </li>' +
                                       '<br>' + 
                                       '<li> Both flies were consistently more exposed to their PC legs, mostly due to how stable the Apr20 meeting was all year. ' +
                                       'The second fly (NoPc-Pc structure) was likely more stable for trading, but both were similar in terms of their Pc leg vol predominance. </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_8.layout.width = '23%'
DesriptionBox_8.layout.height = '380px'
DesriptionBox_8.layout.left = '-20px'
DesriptionBox_8.layout.top = '40px'


VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'GJK0 / JKN0 flies leg NC distribution and leg volatility (40 day rolling Std) </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure19_2, figure20_2], layout = {'width': '100%'}), 
                               HBox([figure21_2, figure22_2], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_8]), BorderHtmlW])

In [50]:
(figure14_3, figure15_3, figure16_3, figure17_3, figure18_3, 
           figure19_3, figure20_3, figure21_3, figure22_3) = FliesMiniPanel('N20', 40)

DesriptionBox_9 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> The shape of the curve (steeper slope on the front and a flatter back), ' + 
                                       'combined with the presence of PC-bias, specially on the front, meant that Pc-NoPc structures (XFG0 and GJK0) had a consistent ' + 
                                       'negative bias. Moving to the back of the curve, the last two 2020 NoPc meetings displayed a smoother ' +
                                       'relationship with its adjacent meetings (likely curve level related) </li>' +
                                       '<br>' +   
                                       '<li>  Even though we begin seeing a more mean reverting Pc-NoPc fly (KNQ0), the bias was present all year, ' +
                                       ' trading always < 0. ' +
                                       '<br>' +
                                       'The fly reacted on every rally moving to its extremes, but rebounded closer to 0 on every post rally selloff/stable period. ' +
                                       '  </li>' +
                                       '<br>' + 
                                       '<li> The differences between both fly structures are less apparent, both were similar, more mean  ' +
                                       'reverting and quite stable as the slope was smoother and less prone to strong reactions to the strongest rallies of the year. ' +
                                       'Selloffs proved to be good opportunities for favorable rolldown and shock friendly shorts, on both cases. </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_9.layout.width = '23%'
DesriptionBox_9.layout.height = '380px'
DesriptionBox_9.layout.left = '-20px'
DesriptionBox_9.layout.top = '40px'


VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'Jul20 (N20) hike time series and KNQ0 / NQV0 flies </p>'),
      BorderHtmlW, HBox([VBox([figure14_3, 
                               HBox([figure15_3, figure16_3], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_9]), BorderHtmlW])

In [51]:
DesriptionBox_10 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> On this section of the curve, daily leg net change behaviour was more homogeneous on both fly structures (Pc-NoPc and NoPc-Pc). ' + 
                                       'The fly KNQ0 still had similarities with XFG0 and GJK0 (same structure), with a fatter tail on the negative NC side of its ' + 
                                       'front leg (KN20 cal), and a larger share of its volatility associated with that same leg </li>' +
                                       '<br>' +   
                                       '<li> On the NQV0 fly we see, for the first time, a larger share of its vol associated with the NoPc leg (cal NQ0), ' + 
                                       'the bias was consistent all year until the May/Jun rally, but quickly readjusted by July </li>' +
                                       '<br>' + 
                                       '<li> More stable and mean-reverting spreads, due to a flatter section of the curve, made them more tradeable. ' + 
                                       'There werent significant differences between both structures (Pc-NoPc and NoPc-Pc), ' +
                                       'their main difference was that the KNQ0 fly was more exposed to its Pc leg while the opposite was the norm for NQV0. ' +
                                       'This is consistent with a front-leg bias, which would be expected on a smoother positive sloped curve, ' + 
                                       'impliying favorable rolldows </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_10.layout.width = '23%'
DesriptionBox_10.layout.height = '380px'
DesriptionBox_10.layout.left = '-20px'
DesriptionBox_10.layout.top = '40px'

VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'KNQ0 / NQV0 flies leg NC distribution and leg volatility (40 day rolling Std) </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure19_3, figure20_3], layout = {'width': '100%'}), 
                               HBox([figure21_3, figure22_3], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_10]), BorderHtmlW])

In [52]:
(figure14_4, figure15_4, figure16_4, figure17_4, figure18_4, 
           figure19_4, figure20_4, figure21_4, figure22_4) = FliesMiniPanel('V20', 40)

DesriptionBox_11 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> Both flies were relatively well behaved all year, like KNQ0 and NQV0, except for a ~2 month period starting by mid June, ' +
                                       'right after the May FOMC minutes rally. ' + 
                                       '<br>' +                                
                                       'The Nov20 Meeting remained anchored and nearly unchanged for that period while the ' +
                                       'rest of the curve kept on sliding down (Jul20 experienced a similar situation, but not as persistent).' + 
                                       '<br>' +
                                       'Both flies swiftly moved, dragged by the Pc-meeting exposed leg (Sept20 and Dec20 meetings). Moving to extreme values by early August ' +
                                       'and then swiftly correcting back to their normal range. This could have been related to 2020 Presidential Elections (Nov 5th)  </li>' +
                                       '<br>' + 
                                       '<li> Same as for the Jul20 hike. Both fly structures were similar, stable and mean reverting' +
                                       'except for the Jun-Aug blip, due to the smoother slope and less exposure to market swings </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_11.layout.width = '23%'
DesriptionBox_11.layout.height = '380px'
DesriptionBox_11.layout.left = '-20px'
DesriptionBox_11.layout.top = '40px'

VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' +  
                   'Nov20 (X20) hike time series and QVX0 / VXF1 flies </p>'),
      BorderHtmlW, HBox([VBox([figure14_4, 
                               HBox([figure15_4, figure16_4], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_11]), BorderHtmlW])

In [53]:
DesriptionBox_12 = widgets.HTML('<p>' +                            
                                   '<ul style = "color: #125CB2; font-size: 14px; font-weight: bold;">' + 
                                       '<li> Again, the flatter and less noisy section of the curve meant daily leg net change behaviour was more ' + 
                                       'homogeneous on both fly structures (Pc-NoPc and NoPc-Pc) </li>' + 
                                       '<br>' +   
                                       '<li> For both flies (QVX0 and VXF1) a larger share of their vol was associated with the Pc leg (cal QV0 and XF1), ' + 
                                       'but the bias was less consistent </li>' +
                                       '<br>' + 
                                       '<li> Again, these spreads were more stable, mean-reverting and tradeable than their front-most counterparts. ' +
                                       '<br>' +
                                       'There werent significant differences between both structures (Pc-NoPc and NoPc-Pc)  </li>' +
                                       '<br>' +
                                       '<li> The peak for spread vol associated with the Pc leg on both cases was the Jun to Aug period, where the Nov20 meeting was ' +
                                       'nearly unchanged for the whole period (mentioned on the previous slide) </li>' +
                                   '</ul>' + 
                               '</p>')

DesriptionBox_12.layout.width = '23%'
DesriptionBox_12.layout.height = '380px'
DesriptionBox_12.layout.left = '-20px'
DesriptionBox_12.layout.top = '40px'

VBox([widgets.HTML('<a id="Figure_9"></a>'),
      widgets.HTML('<p style = "color: #125CB2; font-size: 16px;"> <b> 2020 NoPc Hikes & Strategies Time Series: </b>' + 
                   'QVX0 / VXF1 flies leg NC distribution and leg volatility (40 day rolling Std) </p>'),
      BorderHtmlW, HBox([VBox([HBox([figure19_4, figure20_4], layout = {'width': '100%'}), 
                               HBox([figure21_4, figure22_4], layout = {'width': '100%'})], 
                              layout = {'width': '75%'}), 
                         DesriptionBox_12]), BorderHtmlW])

In [54]:
#FedSpeakBBDD.head()

#wordcloud = WordCloud().generate(FedSpeakBBDD.iloc[:, 3].str.cat())

#import matplotlib.pyplot as plet
#plet.imshow(wordcloud, interpolation='bilinear')
#plet.axis("off")
#plet.show()